In [1]:
import numpy as np
import random
import math
import random

In [2]:
def distance(p1, p2):
  """
  محاسبه فاصله اقلیدسی دو نقطه

  Args:
    p1: نقطه اول
    p2: نقطه دوم

  Returns:
    فاصله اقلیدسی بین دو نقطه
  """

  x1, y1 = p1
  x2, y2 = p2

  dx = x1 - x2
  dy = y1 - y2

  return math.sqrt(dx**2 + dy**2)

In [3]:
def calculate_distance(cities, solution):
    total_distance = 0
    for i in range(len(solution) - 1):
        city1 = cities[solution[i]]
        city2 = cities[solution[i + 1]]
        distance = ((city1[1] - city2[1])**2 + (city1[2] - city2[2])**2)**0.5
        total_distance += distance
    return total_distance


In [4]:
def randomGeneration():
  return np.random.permutation(100)

In [5]:
def read_city_data(filename):
    city_data = []
    with open(filename, 'r') as f:
        for line in f:
            city, lat, lon = line.strip().split(' ')
            city_data.append((city, int(lat), int(lon)))
            # id , lat (x), long(y) in tupple
    return city_data

In [6]:
city_data = read_city_data('city-cor.txt')
print(len(city_data))
# for city, lat, lon in city_data:
#     print(f"City: {city}, Latitude: {lat}, Longitude: {lon}")

100


In [7]:
print(city_data[0])

('1', 1380, 939)


In [8]:
def generate_random_chromosomes(population_size, num_cities=100):
    chromosomes = []
    for _ in range(population_size):
        chromosome = randomGeneration()
        # random.shuffle(chromosome)
        chromosomes.append(chromosome)
    return chromosomes

In [9]:
population = generate_random_chromosomes(500,100)
print(population[0])

[97 51 55 52 16 77 39 90 73 86 85 31  7  9 54  0  3 49 78 22 35 44 14 23
 59 92 83 11 63 82 19 47 66 71 27 61  5  2 91 12 42 57 21 75 88 46 30 20
 62 67 84 34 89 13 69 68 95 33  8 38 15 76 94 58 72 29 17 45 60 96 40 53
 93 25 32 87 64 56 10 70 65 36 80 79 37  4  6 98 74  1 81 18 99 24 26 28
 50 48 43 41]


In [10]:
def calculate_fitness(chromosome, cities=city_data):
    total_distance = 0
    if len(chromosome) != 100 :
      raise ValueError
    for i in range(100):
        city1_index = chromosome[i-1]
        city2_index = chromosome[i]
        
        city1 = cities[city1_index-1]
        city2 = cities[city2_index-1]

        latitude_diff = city1[1] - city2[1]
        longitude_diff = city1[2] - city2[2]

        distance = math.sqrt(latitude_diff**2 + longitude_diff**2)
        total_distance += distance
    return int(total_distance // 1)

In [11]:
calculate_fitness(population[0])

161791

In [12]:
def calculate_fitness_np(chromosome, cities=city_data):
    if len(chromosome) != 100 :
        print('wrong chromosome length')
        raise ValueError

    total_distance = 0
    for i in range(100):
        city1_index = chromosome[i-1]
        city2_index = chromosome[i]
        
        city1 = np.array(cities[city1_index-1][1:])
        city2 = np.array(cities[city2_index-1][1:])
        
        distance = np.linalg.norm(city1 - city2)
        total_distance += distance

    return int(total_distance // 1)

In [13]:
calculate_fitness_np(population[0])

161791

In [14]:
for chro in population :
  # print((chro[99]))
  fitforchro = calculate_fitness(chro)
print(fitforchro)

171776


In [15]:
# fitness_values = []
# for chromosome in population :
#     fitness_value = calculate_fitness(chromosome, cities = city_data)
#     fitness_values.append(fitness_value)
# fitness_values

In [16]:
fitness_values = np.array([calculate_fitness(chromosome, cities=city_data) for chromosome in population])
print(fitness_values)

[161791 173927 168389 186865 158111 171880 173102 174755 174697 159768
 168960 169770 180832 178322 167613 181244 179728 177552 158575 159458
 161523 162079 169017 157141 163824 175026 169366 169071 165939 181344
 163215 181186 181681 181613 181204 176762 178058 169143 174177 170176
 179880 170812 173871 186290 158092 177832 167746 167178 156465 172615
 163055 167182 159859 178326 163645 170976 177177 172095 179869 167425
 165711 165622 167727 162387 173921 176169 163723 172365 178604 171380
 162353 184762 184499 158479 172805 168500 152423 164940 172939 171215
 168651 185708 164721 170434 172047 166061 176717 167797 169137 158286
 160651 183790 166272 174912 155051 173039 161134 168411 167591 173494
 179328 170153 181968 179847 156770 171575 179307 169156 169800 171179
 164457 192587 181433 168996 178122 176882 164446 173690 172778 158321
 167757 175440 168170 158210 167220 171188 168183 167712 174753 182270
 176554 183932 171623 152033 164116 162769 164049 167844 158612 174807
 15899

In [82]:
def permutation_parent_selection(population, fitness_values, selection_method="roulette_wheel"):
  """Selects parents for a genetic algorithm using permutation representation.

  Args:
    population: A list of chromosomes in permutation representation.
    fitness_values: A list of fitness values for each chromosome in the population.
    selection_method: The parent selection method to use. Supported methods are
      "roulette_wheel" and "tournament".

  Returns:
    A tuple of two chromosomes selected as parents.
  """

  if selection_method == "roulette_wheel":
    return roulette_wheel_permutation_parent_selection(population, fitness_values)
  elif selection_method == "tournament":
    return tournament_permutation_parent_selection(population, fitness_values)
  else:
    raise ValueError("Unsupported parent selection method: {}".format(selection_method))


def roulette_wheel_permutation_parent_selection(population, fitness_values):
  """Selects parents using roulette wheel selection for permutation representation.

  Args:
    population: A list of chromosomes in permutation representation.
    fitness_values: A list of fitness values for each chromosome in the population.

  Returns:
    A tuple of two chromosomes selected as parents.
  """

  total_fitness = np.sum(fitness_values)
  fitness_probabilities = fitness_values / total_fitness
  cumulative_probabilities = np.cumsum(fitness_probabilities)

  random_value = random.random()
  parent1_index = 0
  for i, probability in enumerate(cumulative_probabilities):
    if random_value < probability:
      parent1 = population[i]
      break

  random_value = random.random()
  parent2_index = 0
  for i, probability in enumerate(cumulative_probabilities):
    if random_value < probability:
      parent2 = population[i]
      break

  return parent1, parent2


def tournament_permutation_parent_selection(population, fitness_values, tournament_size=2):
  """Selects parents using tournament selection for permutation representation.

  Args:
    population: A list of chromosomes in permutation representation.
    fitness_values: A list of fitness values for each chromosome in the population.
    tournament_size: The size of the tournament.

  Returns:
    A tuple of two chromosomes selected as parents.
  """

  parent1 = None
  parent2 = None

  for _ in range(tournament_size):
    random_index = random.randint(0, len(population) - 1)

    if parent1 is None or fitness_values[random_index] > fitness_values[parent1]:
      parent1 = population[random_index]

    if parent2 is None or fitness_values[random_index] > fitness_values[parent2]:
      parent2 = population[random_index]

  return parent1, parent2


In [18]:
roulette_wheel_permutation_parent_selection(population=population, fitness_values=fitness_values)

(array([75, 67,  1, 70, 56, 55, 54,  4, 86, 51, 35, 26, 39, 99, 42, 22, 46,
        14, 53,  3, 98, 65, 94, 18, 62, 77, 27,  9, 93, 88,  5, 48, 15, 36,
         2, 97, 20, 81, 95, 59, 10, 96, 68, 33, 24, 66, 52, 28, 45, 79, 47,
        44, 74, 71, 30, 37, 76, 38, 87, 19, 43,  0, 78, 21, 60, 72,  6, 31,
        49, 12, 11,  8, 64, 25, 84, 90, 50, 91, 29, 41, 83, 23, 16, 89, 80,
        92, 85, 57, 82, 13, 17, 58, 63,  7, 40, 34, 61, 73, 32, 69]),
 array([62, 35, 97,  2, 46, 28, 92, 81, 40, 36, 25, 23, 33, 83, 96, 87, 85,
        64, 27, 49,  5, 91, 10, 37, 39, 34, 13,  9, 59, 53, 56, 29, 75, 26,
        58, 66,  1, 99, 42, 20, 78, 43, 18, 63, 73, 93,  6, 45, 79,  7, 69,
        94, 15, 80, 74, 50, 95, 17, 67,  3, 54, 12, 14, 61, 11, 90, 47, 16,
        77, 48,  8, 19, 22, 98, 76, 31, 41, 52, 68,  0, 57, 88, 89, 55, 30,
        70, 71, 32, 65, 44,  4, 21, 86, 82, 24, 38, 51, 84, 60, 72]))

In [52]:
import numpy as np

def PMX_crossover(firstPermutation, secondPermutation):
    length = len(firstPermutation)
    
    first_Cross = np.random.randint(0, length // 2)
    second_Cross = np.random.randint(length // 2 + 1, length) + 1

    if first_Cross >= second_Cross:
        # swap the crossover points if necessary
        first_Cross, second_Cross = second_Cross, first_Cross
    
    segment1 = firstPermutation[first_Cross:second_Cross]
    segment2 = secondPermutation[first_Cross:second_Cross]
    mapping = np.zeros(length, dtype=int)
    
    for i in range(len(segment1)):
        mapping[segment1[i]] = segment2[i]
        mapping[segment2[i]] = segment1[i]
    # if np.unique(mapping).size != length:
    #     # raise an error if the mapping array is invalid
    #     raise ValueError("Invalid mapping array")
    child1 = np.zeros(length, dtype=int)
    child2 = np.zeros(length, dtype=int)
    
    for i in range(length):
        if i >= first_Cross and i <= second_Cross:
            child1[i] = segment2[i - first_Cross - 1 ] # use i - first_Cross here
            child2[i] = segment1[i - first_Cross - 1] # use i - first_Cross here
        else:
            if mapping[firstPermutation[i]] == 0:
                child1[i] = firstPermutation[i]
            else:
                child1[i] = mapping[firstPermutation[i]]
            
            if mapping[secondPermutation[i]] == 0:
                child2[i] = secondPermutation[i]
            else:
                child2[i] = mapping[secondPermutation[i]]
    
    return child1, child2


In [53]:
offspring1, offspring2 = PMX_crossover(population[0], population[1])
print("Offspring 1:", offspring1)
print("Offspring 2:", offspring2)

Offspring 1: [32 51 55 80 16  4 39 90 94 40 85 31 93  6 54 42 69 49 58 65 35 64 14 23
 59 20 83 21 63 82 19 98 66 71 27 61  5  2 91 47 42  0 21 11 53 67  4 87
 92 10 75 65 96 89 50  3 80  6 26 28 24 79 62 73 78 72 68 95 98 43 60 86
  8  7 70 97 69 44 48 81 17 22 76 52 74 37 77  9 47  1 10 18 99 38 33  8
 13 56 60 41]
Offspring 2: [92  5 44 63 42 82 54 98 19 51 68 90 91 87  7 23  4 78 16 35 41 39 67 21
 76 26  1 59 83 31 99 18 50 14 97 48 86 27  2 98 12 42 57 21 75 88 46 30
 20 62 67 84 34 89 13 69 68 95 33  8 38 15 76 94 58 72 29 17 45 60 96 40
 53 93 25 32 87 64 56 10 70 65 36 80 79 37  4  6 98 79 24 66 73 61 96 65
 71 49 85 55]


In [54]:
firstPermutation = np.random.permutation(100) # generate a random permutation of integers from 0 to 99
print(firstPermutation.shape)
secondPermutation = np.random.permutation(100) # generate another random permutation of integers from 0 to 99
PMX_crossover(firstPermutation, secondPermutation) # apply the PMX

(100,)


(array([93, 59, 34, 75, 35, 56, 84, 12, 58, 17, 18, 42, 91,  5, 31, 20, 23,
        80, 26, 60, 68, 85, 55, 88, 40, 72, 44, 99, 63, 21, 11, 19, 79,  2,
        69, 22, 36, 75, 57, 63,  7, 96, 71, 95, 78, 46, 36, 54, 74,  8, 65,
        51, 86, 19, 67, 61, 33, 79,  1, 69, 43, 94,  2, 70, 16, 98, 59, 64,
        27, 92, 28,  9, 87, 37, 41, 73, 32, 47, 58, 76, 23,  3, 53, 52, 17,
        30, 11, 97, 48, 50,  0, 24, 89, 49, 82, 38, 29, 75,  4, 29]),
 array([ 5, 16, 56, 97, 52, 73, 26, 40, 42, 84, 55,  2, 31,  8, 89, 69, 92,
        29, 47, 99, 79, 41, 85, 22, 93, 75, 59, 72, 32, 64, 21, 38, 60, 71,
        36, 51, 74,  6, 65, 32, 36, 49,  4, 79, 63, 38, 90, 29, 91, 88,  3,
        12, 52, 87, 57, 33, 86, 10,  2, 25, 98, 23, 81, 17, 68, 53, 39, 34,
        76, 44, 19, 69, 97, 83, 18, 80, 14, 77, 96, 67, 66, 46, 47, 62, 37,
        75,  0, 15, 61, 59, 48, 35, 20, 27, 58, 13, 45,  6, 37, 24]))

In [62]:
def cxPartialyMatched(ind1, ind2):
    size = min(len(ind1), len(ind2))
    p1, p2 = [0] * size, [0] * size

    # Initialize the position of each indices in the individuals
    for i in range(size):
        p1[ind1[i]] = i
        p2[ind2[i]] = i
    # Choose crossover points
    cxpoint1 = random.randint(0, size)
    cxpoint2 = random.randint(0, size - 1)
    if cxpoint2 >= cxpoint1:
        cxpoint2 += 1
    else:  # Swap the two cx points
        cxpoint1, cxpoint2 = cxpoint2, cxpoint1

    # Apply crossover between cx points
    for i in range(cxpoint1, cxpoint2):
        # Keep track of the selected values
        temp1 = ind1[i]
        temp2 = ind2[i]
        # Swap the matched value
        ind1[i], ind1[p1[temp2]] = temp2, temp1
        ind2[i], ind2[p2[temp1]] = temp1, temp2
        # Position bookkeeping
        p1[temp1], p1[temp2] = p1[temp2], p1[temp1]
        p2[temp1], p2[temp2] = p2[temp2], p2[temp1]

    return ind1, ind2
offspring1, offspring2 = cxPartialyMatched(population[0], population[1])
print("Offspring 1:", offspring1)
print("Offspring 2:", offspring2)

Offspring 1: [52 81 16 90 42 35 77 86 12 73 15 61 72  2 30 70 34 45 89 36 13 49 27 59
 47 75 93 88 74 71 76 22 51 56 92 53 62 19  3 39 55 37 83 46 65 97 78 58
 68 79 94 17 57 64 24 26 38 21 98  0 82 10 18 40 99  5 80 23  9 96 95 44
 20 69 32 11 28  4  1 25 85 67  8 87 31 91 29 84 66 48 50 43 60 14 41 33
  7 63 54  6]
Offspring 2: [73 83 75 85  4 10 57 26 74 69 61 60 37 51 25  1 44 94 47 53 36 89 39  0
 24 78 81 91 67 22 50 12 80 15 41 82 19  3 88 18 72 84 55 90 56 23 27 30
  9 28 40 92 68  7 45 62 38  8 29  5 76 71 77 14 58 93 11 65 35 66 32 59
  6 79 13 63 16 96 87 46 34 52 43 21 49 17  2 70 64 33 86 95 31 48 99 98
 20 42 54 97]


In [23]:
def erx_crossover(parent1, parent2):
    """Performs Edge Recombination Crossover (ERX) on two chromosomes.

    Args:
        parent1: The first parent chromosome.
        parent2: The second parent chromosome.

    Returns:
        A new chromosome resulting from the crossover.
    """

    offspring = []
    visited = set()

    # Start from a random gene in parent1
    gene = random.choice(parent1)
    offspring.append(gene)
    visited.add(gene)

    while len(offspring) < len(parent1):
        # Find the next gene to add
        next_gene = None

        # Check if the next gene in parent2 is not in the visited set
        next_gene_in_parent2 = parent2[(parent1.index(gene) + 1) % len(parent1)]
        if next_gene_in_parent2 not in visited:
            next_gene = next_gene_in_parent2

        # Check if the next gene in parent1 is not in the visited set
        if next_gene is None:
            next_gene_in_parent1 = parent1[(parent2.index(gene) + 1) % len(parent2)]
            if next_gene_in_parent1 not in visited:
                next_gene = next_gene_in_parent1

        # If no valid next gene found, break
        if next_gene is None:
            break

        # Add the next gene to the offspring and mark it as visited
        offspring.append(next_gene)
        visited.add(next_gene)

        # Update the current gene
        gene = next_gene

    return offspring

In [24]:
def ox_crossover(parent1, parent2):
    """Performs Order Crossover (OX) on two chromosomes.

    Args:
        parent1: The first parent chromosome.
        parent2: The second parent chromosome.

    Returns:
        A new chromosome resulting from the crossover.
    """

    crossover_points = random.sample(range(1, len(parent1)), 2)
    slice_start, slice_end = crossover_points[0], crossover_points[1]

    slice1 = parent1[slice_start:slice_end]
    remaining_genes1 = set(parent1) - set(slice1)

    mapping = {}
    for i in range(slice_start, slice_end):
        gene1 = parent1[i]
        gene2 = parent2[i]

        if gene1 in remaining_genes1:
            mapping[gene1] = gene2
            remaining_genes1.remove(gene1)

    offspring = []
    for gene in parent2:
        if gene in mapping:
            offspring.append(mapping[gene])
        elif gene not in slice1:
            offspring.append(gene)

    for gene in slice1:
        offspring.append(gene)

    return offspring

In [25]:
def cycle_crossover(parent1, parent2):
    """
    Performs Cycle Crossover (CX) on two chromosomes.

    Args:
        parent1: The first parent chromosome.
        parent2: The second parent chromosome.

    Returns:
        A new chromosome resulting from the crossover.
    """

    cycle_start = random.randrange(len(parent1))
    cycle_genes1 = set(parent1[cycle_start:])
    cycle_genes2 = set(parent2[cycle_start:])

    offspring = list(parent1[:cycle_start])
    for gene in parent2:
        if gene in cycle_genes1:
            offspring.append(gene)
            cycle_genes1.remove(gene)

            if not cycle_genes1:
                break
        else:
            cycle_genes2.add(gene)

    for gene in cycle_genes2:
        offspring.append(gene)

    return offspring

In [23]:
def swap_mutation(chromosome):
    """Performs Swap mutation on a chromosome.

    Args:
        chromosome: The chromosome to mutate.

    Returns:
        A mutated chromosome.
    """

    i, j = random.sample(range(len(chromosome)), 2)
    chromosome[i], chromosome[j] = chromosome[j], chromosome[i]
    return chromosome

In [24]:
def scramble_mutation(chromosome):
    """Performs Scramble mutation on a chromosome.

    Args:
        chromosome: The chromosome to mutate.

    Returns:
        A mutated chromosome.
    """

    mutation_length = random.randrange(2, len(chromosome))
    start_index = random.randrange(len(chromosome) - mutation_length)

    sub_chromosome = chromosome[start_index:start_index + mutation_length]
    random.shuffle(sub_chromosome)
    chromosome[start_index:start_index + mutation_length] = sub_chromosome

    return chromosome

In [25]:
def insert_mutation(chromosome):
    """Performs Insert mutation on a chromosome.

    Args:
        chromosome: The chromosome to mutate.

    Returns:
        A mutated chromosome.
    """

    i = random.randrange(len(chromosome))
    j = random.randrange(len(chromosome))

    if i != j:
        gene = chromosome.pop(i)
        chromosome.insert(j, gene)

    return chromosome

In [26]:
def inversion_mutation(chromosome):
    """Performs Inversion mutation on a chromosome.

    Args:
        chromosome: The chromosome to mutate.

    Returns:
        A mutated chromosome.
    """

    mutation_length = random.randrange(2, len(chromosome))
    start_index = random.randrange(len(chromosome) - mutation_length)

    sub_chromosome = chromosome[start_index:start_index + mutation_length]
    sub_chromosome.reverse()
    chromosome[start_index:start_index + mutation_length] = sub_chromosome

    return chromosome

In [35]:
import numpy as np

def inversion_mutation(permutation):
  # randomly select two positions in the permutation
  i, j = np.random.choice(len(permutation), size=2, replace=False)
  # make sure i is smaller than j
  if i > j:
    i, j = j, i
  # invert the segment between i and j
  permutation[i:j+1] = permutation[i:j+1][::-1]
  return permutation


In [75]:
import numpy as np

def inversion_mutation(chromosome):
  """Performs inversion mutation on a permutation chromosome.

  Args:
    chromosome: A NumPy array of city indices in permutation representation.

  Returns:
    A NumPy array of city indices in permutation representation representing the mutated chromosome.
  """

  # Select two random indices in the chromosome.
  index1 = np.random.randint(0, len(chromosome))
  index2 = np.random.randint(0, len(chromosome))

  # Ensure that the two indices are different.
  while index1 == index2:
    index2 = np.random.randint(0, len(chromosome))

  # Reverse the order of the genes between the two indices.
  # print(type(chromosome[index1:index2 + 1]))
  chromosome[index1:index2 + 1] = chromosome[index1:index2 + 1][::-1]

  return chromosome


# Fake data
chromosome = np.array([1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

# Mutate the chromosome
mutated_chromosome = inversion_mutation(chromosome)

# Print the mutated chromosome
print(mutated_chromosome)


[ 8  7  6  5  4  3  2  1  9 10]


In [41]:
# import unittest
# import numpy as np

# def inversion_mutation(permutation):
#     print('permutation is : ')
#     print(permutation)
#     # randomly select two positions in the permutation
#     i, j = np.random.choice(len(permutation), size=2, replace=False)
#     # make sure i is smaller than j
#     if i > j:
#         i, j = j, i
#     # invert the segment between i and j
#     permutation[i:j+1] = permutation[i:j+1][::-1]
#     return permutation

# class TestInversionMutation(unittest.TestCase):
#     def test_inversion_mutation(self):
#         # Test case 1: permutation with length 5
#         permutation = [1, 2, 3, 4, 5]
#         mutated_permutation = inversion_mutation(permutation)
#         self.assertEqual(len(mutated_permutation), len(permutation))
#         self.assertNotEqual(mutated_permutation, permutation)

#         # Test case 2: permutation with length 10
#         permutation = [10, 9, 8, 7, 6, 5, 4, 3, 2, 1]
#         mutated_permutation = inversion_mutation(permutation)
#         self.assertEqual(len(mutated_permutation), len(permutation))
#         self.assertNotEqual(mutated_permutation, permutation)

# if __name__ == '__main__':
#     unittest.main()


In [80]:
# def roulette_wheel_selection(population, fitness_values):
#     total_fitness = np.sum(fitness_values)
#     fitness_probabilities = fitness_values / total_fitness
#     cumulative_probabilities = np.cumsum(fitness_probabilities)

#     random_index = random.random()
#     for i, probability in enumerate(cumulative_probabilities):
#         # print(f'i is {i}')
#         if random_index < probability:
#             return population[i]
# def roulette_wheel_selection(population, fitness_values):
#     total_fitness = np.sum(fitness_values)
#     fitness_probabilities = fitness_values / total_fitness
#     cumulative_probabilities = np.cumsum(fitness_probabilities)

#     random_value = random.random()
#     for i, probability in enumerate(cumulative_probabilities):
#         if random_value < probability:
#             selected_chromosome = population[i]
#             break

#     # Shuffle the selected chromosome to ensure no bias in selecting the next parent
#     # np.random.shuffle(selected_chromosome)

#     return selected_chromosome

# def tournament_selection(population , cities = city_data, tournament_size = 5):
#     # Create a tournament
#     tournament = random.sample(population, tournament_size)
#     # Select the best individual among the tournament
#     best_individual = min(tournament, key=lambda x: calculate_distance(cities, x))
#     return best_individual

def genetic_algorithm(population_size=500, crossover_rate=0.7, mutation_rate=0.1, max_generations=700,cities = city_data):
    chromosomes = generate_random_chromosomes(500,100)
    print(len(chromosomes))
    fitness_values = []
    for chromosome in chromosomes :
        fitness_value = calculate_fitness_np(chromosome, cities)
        fitness_values.append(fitness_value)

    generation_without_improvement = 0

    for generation in range(max_generations):
        # Select parents using roulette wheel selection
        parents = []
        for i in range(population_size):
            parent1 , parent2 = permutation_parent_selection(chromosomes, fitness_values)
            parents.append((parent1, parent2))

        offsprings = []
        for parent1, parent2 in parents:
            # print(parent1)
            # break
            if random.random() < crossover_rate:
                offspring1 ,offspring2 = PMX_crossover(parent1, parent2)
                #  = PMX_crossover(parent1, parent2)
            else:
                offspring1 = parent1
                offspring2 = parent2

            offsprings.append(offspring1)
            offsprings.append(offspring2)

        # Apply mutation
        for offspring in offsprings:
            if random.random() < mutation_rate:
                # print('offspring is' )
                # print(type(offspring) )
                offspring = inversion_mutation(offspring)

        # Evaluate offspring fitness
        offspring_fitness_values = []
        for offspring in offsprings :
            calculate_fitness(offspring, cities)
            offspring_fitness_value = calculate_fitness_np(offspring, cities)
            print(offspring_fitness_value)
            offspring_fitness_values.append(offspring_fitness_value)

        # Combine parents and offspring to form a new population
        new_population = np.empty_like(chromosomes)
        new_fitness_values = np.empty_like(fitness_values)

        for i in range(population_size):
            if offspring_fitness_values[i] < fitness_values[i]:
                new_population[i] = offsprings[i]
                new_fitness_values[i] = offspring_fitness_values[i]
            else:
                new_population[i] = chromosomes[i]
                new_fitness_values[i] = fitness_values[i]

        chromosomes = new_population
        fitness_values = new_fitness_values

        # Check for stopping condition
        if np.array_equal(fitness_values, offspring_fitness_values):
            generation_without_improvement += 1

            if generation_without_improvement >= 20:
                break
        else:
            generation_without_improvement = 0

    best_chromosome = chromosomes[fitness_values.argmax()]
    best_fitness = np.min(fitness_values)

    return best_chromosome, best_fitness


In [83]:
result = genetic_algorithm()

500
170622
169744
179055
165794
178180
170635
166379
184128
170533
180342
157599
180662
162435
158458
156789
172572
162544
171980
181500
164074
156536
161479
176082
170131
174656
154714
187570
173914
176674
175641
165281
159812
170426
153737
165073
160730
154012
170873
167121
176181
167826
167631
176988
174966
167375
185349
174333
164830
178839
160192
166618
184512
174436
176380
197955
169222
192032
187425
182929
159029
173863
165701
180696
167673
168117
168253
182151
158064
170635
183132
186752
181815
191249
176516
160090
195892
153452
181164
178651
180942
167426
166247
162587
187464
162000
170568
170704
175851
159797
160858
166164
160169
177163
181237
175773
186951
170954
154119
170428
194040
170229
181915
170459
170434
170381
156549
179684
168352
172572
173447
169139
176201
156157
166957
176659
158239
173135
159375
180159
167532
167043
159274
171009
182729
181915
148997
163610
185696
169708
164219
182299
161732
159685
169796
171411
164973
167393
170247
165369
158001
163012
180320
16

KeyboardInterrupt: 